# Project 6: Analyzing Stock Sentiment from Twits
## Instructions
Each problem consists of a function to implement and instructions on how to implement the function.  The parts of the function that need to be implemented are marked with a `# TODO` comment.

## Packages
When you implement the functions, you'll only need to you use the packages you've used in the classroom, like [Pandas](https://pandas.pydata.org/) and [Numpy](http://www.numpy.org/). These packages will be imported for you. We recommend you don't add any import statements, otherwise the grader might not be able to run your code.

### Load Packages

In [1]:
import json
import nltk
import os
import random
import re
import torch

from torch import nn, optim
import torch.nn.functional as F

## Introduction
When deciding the value of a company, it's important to follow the news. For example, a product recall or natural disaster in a company's product chain. You want to be able to turn this information into a signal. Currently, the best tool for the job is a Neural Network. 

For this project, you'll use posts from the social media site [StockTwits](https://en.wikipedia.org/wiki/StockTwits). The community on StockTwits is full of investors, traders, and entrepreneurs. Each message posted is called a Twit. This is similar to Twitter's version of a post, called a Tweet. You'll build a model around these twits that generate a sentiment score.

We've collected a bunch of twits, then hand labeled the sentiment of each. To capture the degree of sentiment, we'll use a five-point scale: very negative, negative, neutral, positive, very positive. Each twit is labeled -2 to 2 in steps of 1, from very negative to very positive respectively. You'll build a sentiment analysis model that will learn to assign sentiment to twits on its own, using this labeled data.

The first thing we should to do, is load the data.

## Import Twits 
### Load Twits Data 
This JSON file contains a list of objects for each twit in the `'data'` field:

```
{'data':
  {'message_body': 'Neutral twit body text here',
   'sentiment': 0},
  {'message_body': 'Happy twit body text here',
   'sentiment': 1},
   ...
}
```

The fields represent the following:

* `'message_body'`: The text of the twit.
* `'sentiment'`: Sentiment score for the twit, ranges from -2 to 2 in steps of 1, with 0 being neutral.


To see what the data look like by printing the first 10 twits from the list. 

In [2]:
with open(os.path.join('..', '..', 'data', 'project_6_stocktwits', 'twits.json'), 'r') as f:
    twits = json.load(f)

print(twits['data'][:10])

[{'message_body': '$FITB great buy at 26.00...ill wait', 'sentiment': 2, 'timestamp': '2018-07-01T00:00:09Z'}, {'message_body': '@StockTwits $MSFT', 'sentiment': 1, 'timestamp': '2018-07-01T00:00:42Z'}, {'message_body': '#STAAnalystAlert for $TDG : Jefferies Maintains with a rating of Hold setting target price at USD 350.00. Our own verdict is Buy  http://www.stocktargetadvisor.com/toprating', 'sentiment': 2, 'timestamp': '2018-07-01T00:01:24Z'}, {'message_body': '$AMD I heard there’s a guy who knows someone who thinks somebody knows something - on StockTwits.', 'sentiment': 1, 'timestamp': '2018-07-01T00:01:47Z'}, {'message_body': '$AMD reveal yourself!', 'sentiment': 0, 'timestamp': '2018-07-01T00:02:13Z'}, {'message_body': '$AAPL Why the drop? I warren Buffet taking out his position?', 'sentiment': 1, 'timestamp': '2018-07-01T00:03:10Z'}, {'message_body': '$BA bears have 1 reason on 06-29 to pay more attention https://dividendbot.com?s=BA', 'sentiment': -2, 'timestamp': '2018-07-01T

### Length of Data
Now let's look at the number of twits in dataset. Print the number of twits below.

In [3]:
"""print out the number of twits"""
# TODO Implement - DONE
print(len(twits['data']))

1548010


### Split Message Body and Sentiment Score

In [4]:
messages = [twit['message_body'] for twit in twits['data']]
# Since the sentiment scores are discrete, we'll scale the sentiments to 0 to 4 for use in our network
sentiments = [twit['sentiment'] + 2 for twit in twits['data']]

## Preprocessing the Data
With our data in hand we need to preprocess our text. These twits are collected by filtering on ticker symbols where these are denoted with a leader $ symbol in the twit itself. For example,

`{'message_body': 'RT @google Our annual look at the year in Google blogging (and beyond) http://t.co/sptHOAh8 $GOOG',
 'sentiment': 0}`

The ticker symbols don't provide information on the sentiment, and they are in every twit, so we should remove them. This twit also has the `@google` username, again not providing sentiment information, so we should also remove it. We also see a URL `http://t.co/sptHOAh8`. Let's remove these too.

The easiest way to remove specific words or phrases is with regex using the `re` module. You can sub out specific patterns with a space:

```python
re.sub(pattern, ' ', text)
```
This will substitute a space with anywhere the pattern matches in the text. Later when we tokenize the text, we'll split appropriately on those spaces.

### Pre-Processing

In [5]:
nltk.download('wordnet')


def preprocess(message):
    """
    This function takes a string as input, then performs these operations: 
        - lowercase
        - remove URLs
        - remove ticker symbols 
        - removes punctuation
        - tokenize by splitting the string on whitespace 
        - removes any single character tokens
    
    Parameters
    ----------
        message : The text message to be preprocessed.
        
    Returns
    -------
        tokens: The preprocessed text into tokens.
    """ 
    #TODO: Implement - Done
    
    # Lowercase the twit message
    text = message.lower()
    
    # Replace URLs with a space in the message
    text = re.sub(r'https?\S', ' ', text) 

    # Replace ticker symbols with a space. The ticker symbols are any stock symbol that starts with $.
    text = re.sub(r'\$[\w]*', ' ', text) 

    # Replace StockTwits usernames with a space. The usernames are any word that starts with @.
    text = re.sub(r'@[\w]*', ' ', text)

    # Replace everything not a letter with a space
    text = re.sub(r'[^a-z]', ' ', text)  
    
    # Tokenize by splitting the string on whitespace into a list of words
    tokens = text.split()

    # Lemmatize words using the WordNetLemmatizer. 
    # You can ignore any word that is not longer than one character.
    wnl = nltk.stem.WordNetLemmatizer()
    tokens = [wnl.lemmatize(word) for word in tokens if len(word) > 1]
    
    return tokens

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


### Preprocess All the Twits 
Now we can preprocess each of the twits in our dataset. Apply the function `preprocess` to all the twit messages.

In [6]:
# TODO Implement - Done
prepocessed_twits = [preprocess(message) for message in messages]

## Bag of Words

we want to create a vocabulary and count up how often each word appears in our entire corpus. Use the Counter function to count up all the tokens.

In [7]:
# Unpacking List - Nested List Comprehension
total_list_of_words = [val for sublist in prepocessed_twits for val in sublist] 

In [8]:
from collections import Counter
bow = Counter(total_list_of_words)

In [9]:
# A subset of bow looks like:
# Counter({'the': 407578, 'to': 396479, 'amp': 2682, 'what': 80233, 'buy': 80123, 'today': 76732}

### Frequency of Words Appearing in Message
With our vocabulary, now we'll remove some of the most common words such as 'the', 'and', 'it', etc. These words don't contribute to identifying sentiment and are really common, resulting in a lot of noise in our input. If we can filter these out, then our network should have an easier time learning.

We also want to remove really rare words that show up in a only a few twits. Here you'll want to divide the count of each word by the number of messages. Then remove words that only appear in some small fraction of the messages.

In [10]:
"""
Set the following variables:
    freqs
    low_cutoff
    high_cutoff
    K_most_common
"""
# TODO Implement - Done 

# Dictionary that contains the Frequency of words appearing in messages.
# The key is the token and the value is the frequency of that word in the corpus.

total_word_count = len(total_list_of_words)

freqs = {}
for key, value in bow.items():
    freqs[key] = value / total_word_count

In [11]:
# Max and Min Frequencies to set thresholds
print("Max",max(freqs.values()))
print("Min",min(freqs.values()))

Max 0.02038562521775934
Min 5.001650044349631e-08


In [12]:
# 95th percentile 
import numpy as np
list_values = [v for v in freqs.values()]
np.percentile(list_values,95)

4.8015840425756455e-06

In [13]:
# Float that is the frequency cutoff. Drop words with a frequency that is lower or equal to this number (%).
# have changed this to filter out more words to speed up model
low_cutoff = 3e-6

In [14]:
# Integer that is the cut off for most common words. Drop words that are the `high_cutoff` most common words.
high_cutoff = 20 # throwing away top 20 words (not %)

In [15]:
# The k most common words in the corpus. Use `high_cutoff` as the k.
K_most_common = [word[0] for word in bow.most_common(high_cutoff)]

In [16]:
bow.most_common(high_cutoff)[0:5]

[('the', 407578),
 ('to', 396479),
 ('amp', 396051),
 ('com', 361663),
 ('utm', 305644)]

In [17]:
K_most_common[0:5]

['the', 'to', 'amp', 'com', 'utm']

In [18]:
filtered_words = [word for word in freqs if (freqs[word] > low_cutoff and word not in K_most_common)]
print(K_most_common)
len(filtered_words)

['the', 'to', 'amp', 'com', 'utm', 'is', 'for', 'on', 'www', 'of', 'and', 'in', 'this', 'it', 'at', 'will', 'up', 'estimize', 'source', 'stock']


8946

### Updating Vocabulary by Removing Filtered Words
Let's creat three variables that will help with our vocabulary.

In [19]:
"""
Set the following variables:
    vocab
    id2vocab
    filtered
"""
# To-Do - Done

# A dictionary for the `filtered_words`. The key is the word and value is an id that represents the word. 
vocab = {word: ii for ii, word in enumerate(filtered_words,1)}
# vocab looks like:
# {'great': 1, 'buy': 2, 'ill': 3, 'wait': 4, 'staanalystalert': 5}

In [20]:
print(len(vocab))

8946


In [21]:
id2vocab = {ii: word for ii, word in enumerate(filtered_words)}
# id2vocab looks like:
# {0: 'great', 1: 'buy', 2: 'ill', 3: 'wait', 4: 'staanalystalert'}

In [22]:
prepocessed_twits[0:3]

[['great', 'buy', 'at', 'ill', 'wait'],
 [],
 ['staanalystalert',
  'for',
  'jefferies',
  'maintains',
  'with',
  'rating',
  'of',
  'hold',
  'setting',
  'target',
  'price',
  'at',
  'usd',
  'our',
  'own',
  'verdict',
  'is',
  'buy',
  'www',
  'stocktargetadvisor',
  'com',
  'toprating']]

In [23]:
# tokenized with the words not in `filtered_words` removed.
filtered = [ [word for word in twit if word in vocab] for twit in prepocessed_twits]

In [24]:
print(len(filtered))

1548010


In [25]:
# shows preprocessed twits with unnecessary words removed from each twit
filtered[0:3]

[['great', 'buy', 'ill', 'wait'],
 [],
 ['staanalystalert',
  'jefferies',
  'maintains',
  'with',
  'rating',
  'hold',
  'setting',
  'target',
  'price',
  'usd',
  'our',
  'own',
  'verdict',
  'buy',
  'stocktargetadvisor',
  'toprating']]

### Balancing the classes
Let's do a few last pre-processing steps. If we look at how our twits are labeled, we'll find that 50% of them are neutral. This means that our network will be 50% accurate just by guessing 0 every single time. To help our network learn appropriately, we'll want to balance our classes.
That is, make sure each of our different sentiment scores show up roughly as frequently in the data.

What we can do here is go through each of our examples and randomly drop twits with neutral sentiment. What should be the probability we drop these twits if we want to get around 20% neutral twits starting at 50% neutral? We should also take this opportunity to remove messages with length 0.

In [26]:
balanced = {'messages': [], 'sentiments':[]}

n_neutral = sum(1 for each in sentiments if each == 2)
N_examples = len(sentiments)
keep_prob = (N_examples - n_neutral)/4/n_neutral

for idx, sentiment in enumerate(sentiments):
    message = filtered[idx]
    if len(message) == 0:
        # skip this message because it has length zero
        continue
    elif sentiment != 2 or random.random() < keep_prob:
        balanced['messages'].append(message)
        balanced['sentiments'].append(sentiment) 

If you did it correctly, you should see the following result 

In [27]:
n_neutral = sum(1 for each in balanced['sentiments'] if each == 2)
N_examples = len(balanced['sentiments'])
n_neutral/N_examples

0.19610436094880626

Finally let's convert our tokens into integer ids which we can pass to the network.

In [28]:
token_ids = [[vocab[word] for word in message] for message in balanced['messages']]
sentiments = balanced['sentiments']

## Neural Network
Now we have our vocabulary which means we can transform our tokens into ids, which are then passed to our network. So, let's define the network now!

Here is a nice diagram showing the network we'd like to build: 

#### Embed -> RNN -> Dense -> Softmax
### Implement the text classifier
Before we build text classifier, if you remember from the other network that you built in  "Sentiment Analysis with an RNN"  exercise  - which there, the network called " SentimentRNN", here we named it "TextClassifer" - consists of three main parts: 1) init function `__init__` 2) forward pass `forward`  3) hidden state `init_hidden`. 

This network is pretty similar to the network you built expect in the  `forward` pass, we use softmax instead of sigmoid. The reason we are not using sigmoid is that the output of NN is not a binary. In our network, sentiment scores have 5 possible outcomes. We are looking for an outcome with the highest probability thus softmax is a better choice.

In [29]:
class TextClassifier(nn.Module):
    def __init__(self, vocab_size, embed_size, lstm_size, output_size, lstm_layers=1, dropout=0.1):
        """
        Initialize the model by setting up the layers.
        
        Parameters
        ----------
            vocab_size : The vocabulary size.
            embed_size : The embedding layer size.
            lstm_size : The LSTM layer size.
            output_size : The output size. 
            lstm_layers : The number of LSTM layers.
            dropout : The dropout probability.
        """
        
        super().__init__()
        self.vocab_size = vocab_size
        self.embed_size = embed_size
        self.lstm_size = lstm_size
        self.output_size = output_size
        self.lstm_layers = lstm_layers
        self.dropout = dropout
        
        # TODO Implement - Done
        
        # Setup embedding layer
        
        """
        Takes all the words in "vocab" and transforms it to a vector of 
        columns (embed size .. 10 cols in this case) with probability values
        under each column. Simpler than one-hot encoding. 
        Reduces # of dimensions and gain similarity. 
        
        num_embeddings (int) – size of the dictionary of embeddings
        embedding_dim (int) – the size of each embedding vector. 
        """
        self.embedding = nn.Embedding(num_embeddings=vocab_size, embedding_dim=embed_size)
        
        # Setup LSTM layer
        
        """
        Values coming from embedding so embed_size = input_size
        Hidden layer size same as lstm size
        Batch_first=False - with a certain input, it will spit out a certain output. 
        If batch_first=True, would spit out different shape
        Dropout takes out part of the model to avoid overfitting
        """
        self.lstm = nn.LSTM(input_size=embed_size, hidden_size=lstm_size, num_layers=lstm_layers, batch_first=False, dropout=self.dropout)

        # dropout layer
        self.dropout = nn.Dropout(dropout)
        
        # linear and softmax layers
        self.fc = nn.Linear(in_features=lstm_size, out_features=output_size)
        self.logsoft = nn.LogSoftmax(dim=1)


    def init_hidden(self, batch_size):
        """ 
        Initializes hidden state
        
        Parameters
        ----------
            batch_size : The size of batches.
        
        Returns
        -------
            hidden_state
            
        """
        
        # TODO Implement - Done
        
        # Create two new tensors with sizes n_layers x batch_size x hidden_dim,
        # initialized to zero, for hidden state and cell state of LSTM
        
        weight = next(self.parameters()).data
        
        # setting hidden layer weights to zero
        train_on_gpu=torch.cuda.is_available()
        
        
        if (train_on_gpu):
            hidden_state = (weight.new(self.lstm_layers, batch_size, self.lstm_size).zero_().cuda(),
                            weight.new(self.lstm_layers, batch_size, self.lstm_size).zero_().cuda())
        else:
            hidden_state = (weight.new(self.lstm_layers, batch_size, self.lstm_size).zero_(),
                            weight.new(self.lstm_layers, batch_size, self.lstm_size).zero_())
        
        return hidden_state
        

    def forward(self, nn_input, hidden_state):
        """
        Perform a forward pass of our model on nn_input.
        
        Parameters
        ----------
            nn_input : The batch of input to the NN.
            hidden_state : The LSTM hidden state.

        Returns
        -------
            logps: log softmax output
            hidden_state: The new hidden state.

        """
        
        # TODO Implement - Done
        
        """
        Taking the inputs, passing it through embed, passing the embeds through the lstms,
        Takes the last output from the lstm, does dropout, sends to softmax, batch_size changes
        Shape of output, which is returned along with the hidden_state (hidden output of LSTM)
        """

        # embeddings and lstm_out
        nn_input = nn_input.long()
        embeds = self.embedding(nn_input)
        print('embed dimension:', embeds.size())
        
        lstm_out, hidden_state = self.lstm(embeds, hidden_state)
    
        # stack up lstm outputs
        
        """
        Instead of reshaping the lstm_out, pull the last output of LSTM shape (seq_length, batch_size, lstm_size)
        """
        lstm_out = lstm_out[-1, : , :]
        
        # dropout and fully-connected layer
        out = self.dropout(lstm_out)
        out = self.fc(out)
        
        # Softmax function
        logps = self.logsoft(out)
        
        # reshape to be batch_size first
        batch_size = nn_input.size(1)
        logps = logps.view(batch_size, -1)

        # return last sigmoid output and hidden state
        return logps, hidden_state

### View Model

In [30]:
#Set default tensor type, then move model and data to GPU
torch.set_default_tensor_type('torch.cuda.FloatTensor')
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [31]:
model = TextClassifier(len(vocab), 10, 6, 5, dropout=0.1, lstm_layers=2)
model.embedding.weight.data.uniform_(-1, 1)
input = torch.randint(0, 1000, (5, 4), dtype=torch.int64)
hidden = model.init_hidden(4)

logps, _ = model.forward(input, hidden)
print(logps)

embed dimension: torch.Size([5, 4, 10])
tensor([[-1.4829, -1.5238, -1.6760, -1.5721, -1.8300],
        [-1.4531, -1.5472, -1.6874, -1.6138, -1.7769],
        [-1.4237, -1.5180, -1.7314, -1.6831, -1.7304],
        [-1.5104, -1.4362, -1.7442, -1.5900, -1.8162]])


## Training
### DataLoaders and Batching
Now we should build a generator that we can use to loop through our data. It'll be more efficient if we can pass our sequences in as batches. Our input tensors should look like `(sequence_length, batch_size)`. So if our sequences are 40 tokens long and we pass in 25 sequences, then we'd have an input size of `(40, 25)`.

If we set our sequence length to 40, what do we do with messages that are more or less than 40 tokens? For messages with fewer than 40 tokens, we will pad the empty spots with zeros. We should be sure to **left** pad so that the RNN starts from nothing before going through the data. If the message has 20 tokens, then the first 20 spots of our 40 long sequence will be 0. If a message has more than 40 tokens, we'll just keep the first 40 tokens.

In [32]:
def dataloader(messages, labels, sequence_length=30, batch_size=32, shuffle=False):
    """ 
    Build a dataloader.
    """
    if shuffle:
        indices = list(range(len(messages)))
        random.shuffle(indices)
        messages = [messages[idx] for idx in indices]
        labels = [labels[idx] for idx in indices]

    total_sequences = len(messages)

    for ii in range(0, total_sequences, batch_size):
        batch_messages = messages[ii: ii+batch_size]
        
        # First initialize a tensor of all zeros
        batch = torch.zeros((sequence_length, len(batch_messages)), dtype=torch.int64)
        for batch_num, tokens in enumerate(batch_messages):
            token_tensor = torch.tensor(tokens)
            # Left pad!
            start_idx = max(sequence_length - len(token_tensor), 0)
            batch[start_idx:, batch_num] = token_tensor[:sequence_length]
        
        label_tensor = torch.tensor(labels[ii: ii+len(batch_messages)])
        
        yield batch, label_tensor

### Training and  Validation
With our data in nice shape, we'll split it into training and validation sets.

In [33]:
"""
Split data into training and validation datasets. Use an appropriate split size.
The features are the `token_ids` and the labels are the `sentiments`.
"""   

# TODO Implement - Done

split=0.75
split_threshold = int(len(token_ids) * split)

train_features = token_ids[:split_threshold]
valid_features = token_ids[split_threshold:]
train_labels = sentiments[:split_threshold]
valid_labels = sentiments[split_threshold:]

In [34]:
text_batch, labels = next(iter(dataloader(train_features, train_labels, sequence_length=20, batch_size=64)))
model = TextClassifier(len(vocab)+1, 200, 128, 5, dropout=0.)
hidden = model.init_hidden(64)
logps, hidden = model.forward(text_batch, hidden)

embed dimension: torch.Size([20, 64, 200])


### Training
It's time to train the neural network!

In [35]:
# Using NN to classify new twits based on old twits
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# def __init__(self, vocab_size, embed_size, , output_size, lstm_layers=1, dropout=0.1):
model = TextClassifier(len(vocab)+1, # vocab_size
                       1024, # embed_size
                       512,  # lstm_size 
                       5, # output_size based off sentiments
                       lstm_layers=2, 
                       dropout=0.2)
# setup for first train
batch_size = 64
model.embedding.weight.data.uniform_(-1, 1)
hidden = model.init_hidden(batch_size)
model.to(device)
model

TextClassifier(
  (embedding): Embedding(8947, 1024)
  (lstm): LSTM(1024, 512, num_layers=2, dropout=0.2)
  (dropout): Dropout(p=0.2)
  (fc): Linear(in_features=512, out_features=5, bias=True)
  (logsoft): LogSoftmax()
)

In [36]:
batch_size = 256 # orginally 64 but tried 256 to speed up model
epochs = 1 # 4 originally but 1 to speed up model - how many time you run through the entire dataset
learning_rate = 0.001 # what's adjusted in hyperparameter. How much you learn through backprop
clip = 5 # sets maximum slope for magnitude of gradient
print_every = 100 
seq_len = 20 # Not going to take more than 20 words as your input

criterion = nn.NLLLoss() 
optimizer = optim.Adam(model.parameters(), lr=learning_rate) 
model.train() 

for epoch in range(epochs): 
    print(f'Starting epoch {epoch + 1}') 
    
    train_loss = 0
    steps = 0    

    for text_batch, labels in dataloader(train_features, 
                                         train_labels, 
                                         batch_size=batch_size, 
                                         sequence_length=seq_len, 
                                         shuffle=True):
        hidden = model.init_hidden(batch_size=labels.shape[0])

        steps += 1 
       
        text_batch, labels = text_batch.to(device), labels.to(device)
        
        for each in hidden:
            each=each.to(device)
        
        # TODO Implement: Train Model - Done
        model.zero_grad() 
        log_probs, hidden = model.forward(text_batch, hidden)        
        loss = criterion(log_probs, labels)
        loss.backward()  
        nn.utils.clip_grad_norm_(model.parameters(), clip)  
        optimizer.step()
        train_loss += loss.item()  
        
        if steps % print_every == 0:
            model.eval()

            val_losses = []
            accuracy = []
            
            with torch.no_grad():
                for inputs, labels in dataloader(valid_features, 
                                                 valid_labels, 
                                                 batch_size=batch_size, 
                                                 sequence_length=seq_len, 
                                                 shuffle=True):
                    val_h = model.init_hidden(labels.shape[0])
                    
                    inputs, labels = inputs.to(device), labels.to(device)
                    
                    for each in val_h:
                        each.to(device)
                        
                    logps, val_h = model.forward(inputs, val_h)
                    val_loss = criterion(logps, labels)
                    
                    val_losses.append(val_loss.item()) 
                    
                    # Calculate accuracy
                    ps = torch.exp(logps)
                    top_p, top_class = ps.topk(1, dim=1)
                    equals = top_class == labels.view(*top_class.shape)
                    accuracy.append(torch.mean(equals.type(torch.FloatTensor)).item())
                    
                    print("Epoch: {}/{}...".format(epoch+1, epochs),
                          "Step: {}...".format(steps),
                          "Train Loss: {:.6f}...".format(loss.item()),
                          "Val Loss: {:.6f}".format(np.mean(val_losses)),
                          "Accuracy: {:.6f}".format(np.mean(accuracy)))
                    
                    model.train()

Starting epoch 1
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 1024])
embed dimension: torch.Size([20, 256, 

Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.095090 Accuracy: 0.553776
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.097404 Accuracy: 0.552923
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.093588 Accuracy: 0.555176
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.093241 Accuracy: 0.556108
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.092105 Accuracy: 0.556526
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.092524 Accuracy: 0.555804
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.092598 Accuracy: 0.555990
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1

Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096958 Accuracy: 0.556127
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.097246 Accuracy: 0.556274
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.098054 Accuracy: 0.555896
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.097545 Accuracy: 0.556601
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096702 Accuracy: 0.556897
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096723 Accuracy: 0.556836
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096650 Accuracy: 0.556776
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1

Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096264 Accuracy: 0.560034
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096093 Accuracy: 0.559807
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096255 Accuracy: 0.559631
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096206 Accuracy: 0.559600
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096260 Accuracy: 0.559499
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096071 Accuracy: 0.559541
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.096279 Accuracy: 0.559629
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1

Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091751 Accuracy: 0.561094
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091887 Accuracy: 0.560927
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091570 Accuracy: 0.561141
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091330 Accuracy: 0.561215
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091705 Accuracy: 0.561016
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.092107 Accuracy: 0.560921
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1.091884 Accuracy: 0.561130
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 100... Train Loss: 0.944187... Val Loss: 1

...

Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744095 Accuracy: 0.714567
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744085 Accuracy: 0.714578
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743989 Accuracy: 0.714642
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744035 Accuracy: 0.714643
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744012 Accuracy: 0.714627
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744109 Accuracy: 0.714569
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.744159 Accuracy: 0.714533
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val

Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743535 Accuracy: 0.714736
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743451 Accuracy: 0.714780
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743284 Accuracy: 0.714829
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743176 Accuracy: 0.714883
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743152 Accuracy: 0.714897
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743089 Accuracy: 0.714926
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743152 Accuracy: 0.714921
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val

Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743518 Accuracy: 0.714839
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743477 Accuracy: 0.714830
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743449 Accuracy: 0.714844
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743443 Accuracy: 0.714808
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743558 Accuracy: 0.714772
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743508 Accuracy: 0.714794
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743590 Accuracy: 0.714781
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val

Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743371 Accuracy: 0.714932
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743371 Accuracy: 0.714932
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743377 Accuracy: 0.714919
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743355 Accuracy: 0.714915
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743317 Accuracy: 0.714902
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743307 Accuracy: 0.714886
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743341 Accuracy: 0.714873
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val

Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743459 Accuracy: 0.714828
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743519 Accuracy: 0.714797
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743630 Accuracy: 0.714730
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743659 Accuracy: 0.714707
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743749 Accuracy: 0.714652
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743726 Accuracy: 0.714672
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val Loss: 0.743728 Accuracy: 0.714660
embed dimension: torch.Size([20, 256, 1024])
Epoch: 1/1... Step: 3000... Train Loss: 0.854319... Val

## Making Predictions
### Prediction 
Okay, now that you have a trained model, try it on some new twits and see if it works appropriately. Remember that for any new text, you'll need to preprocess it first before passing it to the network. Implement the `predict` function to generate the prediction vector from a message.

In [99]:
def predict(text, model, vocab):
    """ 
    Make a prediction on a single sentence.

    Parameters
    ----------
        text : The string to make a prediction on.
        model : The model to use for making the prediction.
        vocab : Dictionary for word to word ids. The key is the word and the value is the word id.

    Returns
    -------
        pred : Prediction vector
    """    
    
    # TODO Implement
    tokens = preprocess(text) # good 
    
    # Filter non-vocab words
    tokens = [val for val in tokens if val in vocab] # good
    print("filtered words", tokens)
    # Convert words to ids
    tokens = [vocab[val] for val in tokens] # good
    print("filtered word ids", tokens)
        
    text_input = torch.tensor(tokens).unsqueeze(1)
    hidden  = model.init_hidden(text_input.size(1))
    
    logps, _ = model.forward(text_input, hidden) # good
    pred = torch.exp(logps) # good
    
    return pred.to('cpu').detach().numpy()

In [100]:
text = "Google is working on self driving cars, I'm bullish on $goog"
model.eval
model.to(device)
predict(text, model, vocab)

filtered words ['google', 'working', 'self', 'driving', 'car', 'bullish']
filtered word ids [343, 2798, 6521, 1096, 2671, 157]
embed dimension: torch.Size([6, 1, 1024])


array([[  7.99742411e-04,   1.91239268e-02,   1.52642475e-02,
          8.21958065e-01,   1.42854035e-01]], dtype=float32)

### Questions: What is the prediction of the model? What is the uncertainty of the prediction?
** TODO: Answer Question**

Now we have a trained model and we can make predictions. We can use this model to track the sentiments of various stocks by predicting the sentiments of twits as they are coming in. Now we have a stream of twits. For each of those twits, pull out the stocks mentioned in them and keep track of the sentiments. Remember that in the twits, ticker symbols are encoded with a dollar sign as the first character, all caps, and 2-4 letters, like $AAPL. Ideally, you'd want to track the sentiments of the stocks in your universe and use this as a signal in your larger model(s).

## Testing
### Load the Data 

In [93]:
with open(os.path.join('..', '..', 'data', 'project_6_stocktwits', 'test_twits.json'), 'r') as f:
    test_data = json.load(f)

### Twit Stream

In [94]:
def twit_stream():
    for twit in test_data['data']:
        yield twit

next(twit_stream())

{'message_body': '$JWN has moved -1.69% on 10-31. Check out the movement and peers at  https://dividendbot.com?s=JWN',
 'timestamp': '2018-11-01T00:00:05Z'}

Using the `prediction` function, let's apply it to a stream of twits.

In [95]:
def score_twits(stream, model, vocab, universe):
    """ 
    Given a stream of twits and a universe of tickers, return sentiment scores for tickers in the universe.
    """
    for twit in stream:

        # Get the message text
        text = twit['message_body']
        symbols = re.findall('\$[A-Z]{2,4}', text)
        score = predict(text, model, vocab)

        for symbol in symbols:
            if symbol in universe:
                yield {'symbol': symbol, 'score': score, 'timestamp': twit['timestamp']}

In [96]:
universe = {'$BBRY', '$AAPL', '$AMZN', '$BABA', '$YHOO', '$LQMT', '$FB', '$GOOG', '$BBBY', '$JNUG', '$SBUX', '$MU'}
score_stream = score_twits(twit_stream(), model, vocab, universe)

next(score_stream)

['ha', 'moved', 'check', 'out', 'movement', 'peer', 'dividendbot', 'jwn']
[120, 121, 122, 37, 123, 124, 46, 1611]
embed dimension: torch.Size([8, 1, 1024])
['bt', 'put', 'when', 'cramer', 'going', 'so', 'profit', 'bt', 'back', 'yesterday', 'down', 'day', 'good', 'look', 'lower', 'too']
[8136, 264, 204, 4521, 132, 138, 865, 8136, 61, 2681, 536, 115, 49, 321, 977, 129]
embed dimension: torch.Size([16, 1, 1024])
['after', 'er']
[65, 1331]
embed dimension: torch.Size([2, 1, 1024])


{'symbol': '$AAPL',
 'score': array([[ 0.09374435,  0.10287894,  0.18589848,  0.2596522 ,  0.35782605]], dtype=float32),
 'timestamp': '2018-11-01T00:00:18Z'}

That's it. You have successfully built a model for sentiment analysis! 

## Submission
Now that you're done with the project, it's time to submit it. Click the submit button in the bottom right. One of our reviewers will give you feedback on your project with a pass or not passed grade. You can continue to the next section while you wait for feedback.